# DATA Processing

### Import libraries

In [1]:
from plotly import graph_objs as go
from plotly import express as px
from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from matplotlib import cm
from matplotlib.ticker import LinearLocator, FormatStrFormatter
import numpy as np
import pandas as pd
import pywt.data
from scipy import*
from datetime import datetime
from plotly.express.colors import sample_colorscale
from sklearn.preprocessing import minmax_scale
from sklearn.metrics import mean_absolute_percentage_error

pd.options.plotting.backend = "plotly"

#from statsmodels.nonparametric.smoothers_lowess import lowess
from scipy.signal import savgol_filter

### Optical Response

### Loading data

In [2]:
# Function for cleaning
def PM100D_data(file_names: list) -> pd.DataFrame:
    dt = pd.DataFrame()
    for name, index in zip(file_names, np.arange(1, len(file_names)+1)):
        data_optic_response = pd.read_excel(f'{name}', header = None)
        data_optic_response['Timestamp'] = pd.to_timedelta(data_optic_response.iloc[15:, 2]).dt.total_seconds()
        data_optic_response['Timestamp'] = data_optic_response['Timestamp'] - data_optic_response.iloc[15, 5]
        dt[f'optic_response_{index}_Time_s'] = data_optic_response.iloc[15:, 5]
        dt[f'optic_response_{index}_Power_W'] = data_optic_response.iloc[15:, 3]
    dt = dt.reset_index().drop(['index'], axis=1)
    return dt

# Function for cleaning
def PM320_data(file_names: list) -> pd.DataFrame:
    dt = pd.DataFrame()
    for name, index in zip(file_names, np.arange(1, len(file_names)+1)):
        data_optic_response = pd.read_table(f'{name}', header = None, sep = r"\s+")
        dt[f'optic_response_{index}_Time_s'] = data_optic_response.index.values
        dt[f'optic_response_{index}_Power_W'] = data_optic_response.drop([0, 1, 2, 3, 4, 5, 7, 8], axis=1).rename(columns={6: 'Power_dshape'})
        #dt[f'data_optic_response_{index}_Power_ASE'] = data_optic_response.drop([0, 1, 2, 4, 5, 6, 7, 8], axis=1).rename(columns={3: 'Power_ASE'})
    return dt

# Function for cleaning
def old_PM100D_data(file_names: list) -> pd.DataFrame:
    dt = pd.DataFrame()
    for name, index in zip(file_names, np.arange(1, len(file_names)+1)):
        data_optic_response = pd.read_excel(f'{name}', header = None)
        data_optic_response = data_optic_response.iloc[23:, 0:2].rename(columns={0: 'Time_ms', 1: 'Power_W'}).reset_index().drop(['index'], axis=1)
        dt[f'optic_response_{index}_Time_ms'] = data_optic_response.iloc[:, 0]
        dt[f'optic_response_{index}_Power_W'] = data_optic_response.iloc[:, 1]
    return dt

In [3]:
# Input parameters for PM320_data:
file_names_optic = [r'optic_data_20_09_23_new_CNT_HumAir_RH10.xlsx',
                    r'optic_data_20_09_23_new_CNT_HumAir_RH30.xlsx',
                    r'optic_data_20_09_23_new_CNT_HumAir_RH50.xlsx',]


In [4]:
optic_data = PM100D_data(file_names_optic)
optic_data.head()

optic_response_1_Time_s optic_response_1_Power_W  optic_response_2_Time_s  \
0                    0.000                 0.006766                    0.000   
1                    0.264                 0.006766                    1.032   
2                    1.283                 0.006767                    2.055   
3                    2.302                 0.006767                    3.084   
4                    3.314                 0.006766                    4.092   

  optic_response_2_Power_W  optic_response_3_Time_s optic_response_3_Power_W  
0                 0.006842                    0.000                 0.006888  
1                 0.006841                    1.031                 0.006888  
2                  0.00684                    2.049                 0.006886  
3                 0.006841                    3.055                 0.006886  
4                 0.006841                    4.056                 0.006885

### Transmittance

In [5]:
# Initial parameters
time_cycle = 6 # min
not_taken_number_cycles = 1
taken_number_cycles = 8
Power_before_dshape = 0.01123

In [6]:
# Function for creating transmittance data PM100D
def Transmittance_create_data(data: pd.DataFrame):
    Transmittance_norm = pd.DataFrame()
    count = 1
    for n in np.arange(0, len(data.columns), 2):
        Transmittance_0 = data.iloc[0, n+1]
        Transmittance_norm[f'Optic_response_{count}_Transmit'] = (data.iloc[:, n+1] - Transmittance_0) / Transmittance_0
        count += 1
    return Transmittance_norm

# Function for creating time data
def Time_create_data(data):
    Time = pd.DataFrame()
    count = 1
    for n in np.arange(0, len(data.columns), 2):
        Time[f'{count}_Time'] = data.iloc[:, n]
        count += 1
    return Time

In [7]:
Transmittance_norm_data = Transmittance_create_data(optic_data)
Transmittance_norm_data.head()

Optic_response_1_Transmit Optic_response_2_Transmit  \
0                       0.0                       0.0   
1                       0.0                 -0.000161   
2                  0.000163                  -0.00019   
3                  0.000177                 -0.000058   
4                  0.000133                 -0.000058   

  Optic_response_3_Transmit  
0                       0.0  
1                 -0.000073  
2                 -0.000276  
3                 -0.000334  
4                 -0.000406

In [8]:
Time_data_T = Time_create_data(optic_data)
Time_data_T.head()

1_Time  2_Time  3_Time
0   0.000   0.000   0.000
1   0.264   1.032   1.031
2   1.283   2.055   2.049
3   2.302   3.084   3.055
4   3.314   4.092   4.056

In [9]:
# plotting raw data
def quick_plot_T(data: pd.DataFrame, Time_data, time_cycle) -> None:
    fig = go.Figure()
    
    # Making colour for each data
    humidity = [10, 30, 50]
    color_dict = dict(zip(humidity, sample_colorscale('Portland', minmax_scale(humidity))))

    # Creating line plots from data
    for column, humid, count in zip(data.columns.values, humidity, np.arange(0, len(data.columns.values), 1)):
        minutes = Time_data.iloc[:, count].values / 60
        fig.add_trace(go.Scattergl(x = minutes, 
                                   y = data.loc[:,column].values, 
                                   name = str(f'{humid}% humidity'),
                                   line_color = color_dict[humid]))

    # Creating vertical rectangles
    for i in np.arange(time_cycle/2 +0.15, max(Time_data.max())/60, time_cycle):
        fig.add_vrect(x0=i,
                      x1=i + 3,
                      line_width=0,
                      fillcolor='grey',
                      opacity=0.1,
                      annotation_text='<i>H<sub>2</sub></i>O',
                      annotation_font_size=20,
                      annotation_textangle=270,
                      annotation_position='top',)

    # Updating layout data
    fig.update_layout(font_size = 15,
                      title = f"CNT film T=80%, S11=1.5 \u03BCm.  date: 20.09.23 <br>Mixture: Dry Air (100 sccm) <--> Dry Air + Humid Air",
                      legend_title = "Measurement<br>parameters",
                      legend_font_size = 15,
                      xaxis_title = "Time, min",
                      yaxis_title = "Transmittance, \u0394T / T0",
                      #yaxis_type = 'log',
                      plot_bgcolor = 'rgba(250,250,250,1)',
                      width = 950,
                      height = 650,
                      )
    fig.add_shape(type="rect",
                  xref="paper",
                  yref="paper",
                  x0=0,
                  y0=0,
                  x1=1.0,
                  y1=1.0,
            line=dict(
                color="black",
                 width=1,))
    fig.show()

In [10]:
quick_plot_T(Transmittance_norm_data, Time_data_T[Time_data_T.iloc[:, 0] < 3780], time_cycle)

---
### Violin Plots

In [11]:
def print_dt_metrics(Time_data: pd.DataFrame, humidity=[0, 30, 50]):
    try:
        dt = Time_data.diff().dropna()
        time_dt = pd.DataFrame()
        for index, humid in zip(range(0, len(Time_data.columns)), humidity):
            # dt - time between two neighboring datapoints [in seconds]
            time_dt.loc[f'{humid}', 'mean'] = dt.describe().iloc[1, index]
            time_dt.loc[f'{humid}', 'std'] = dt.describe().iloc[2, index]
            
            MAPE = mean_absolute_percentage_error(dt.iloc[:, index], np.array([dt.describe().iloc[1, index]] * len(dt)))
            time_dt.loc[f'{humid}', 'MAPE'] = MAPE * 100 # in percentages %
        
        return time_dt
    except AttributeError:
        print("Cannot calculate metrics: no Time_sec column. Wrong dataframe? Need raw dataframe from load_data")

In [12]:
print_dt_metrics(Time_data_T)

mean       std      MAPE
0   0.999807  0.097372  5.968795
30  0.999997  0.096703  5.890545
50  0.999991  0.096653  5.876199

In [13]:
def violin_plot(Time_data: pd.DataFrame):
  data_metrics = print_dt_metrics(Time_data)
  for index in range(0, len(Time_data.columns)):

    fig = px.scatter(x = Time_data.iloc[1:, index].dropna(), y = Time_data.diff().iloc[:, index].dropna(), marginal_y = "violin")
    # Updating layout data
    fig.update_layout(font_size = 15,
                      title = f"dt = {data_metrics.iloc[index, 0]:.2f} \u00b1 {data_metrics.iloc[index, 1]:.3f} seconds <br> MAPE = {data_metrics.iloc[index, 2]:.2f} %",
                      title_x=0.5,
                      legend_title = "Measurement<br>parameters",
                      legend_font_size = 15,
                      xaxis_title = "Time, s",
                      yaxis_title = "Time difference between datapoints, s",
                      hovermode = False,
                      plot_bgcolor = 'rgba(250,250,250,1)',
                      width = 1200,
                      height = 650,
                      )
    fig.add_shape(type="rect",
                  xref="paper",
                  yref="paper",
                  x0=0,
                  y0=0,
                  x1=1.0,
                  y1=1.0,
            line=dict(
                color="black",
                 width=1,))

    fig.show()

In [14]:
violin_plot(Time_data_T.iloc[1:, :])

---

### Computing Sensor Signal

In [15]:
def sensor_signal(data: pd.DataFrame, name, search_delta=60):
        
    Sensor_signal = pd.DataFrame()
    for index in range(0, len(data.columns), 2):

        #Calculating Sensor signal
        if name == 'Resistance':
            # Min values of air:
            first_3_min = [data.loc[(data.iloc[:, index] < (minutes_3_mark + search_delta)) & (data.iloc[:, index] > (minutes_3_mark - search_delta))].iloc[:, index+1].max() for minutes_3_mark in range(540, int(data.iloc[data.iloc[:, index].last_valid_index(), index]), time_cycle*60)]

            # Max values of gas:
            second_3_min = [data.loc[(data.iloc[:, index] < (minutes_3_mark + search_delta)) & (data.iloc[:, index] > (minutes_3_mark - search_delta))].iloc[:, index+1].min() for minutes_3_mark in range(720, int(data.iloc[data.iloc[:, index].last_valid_index(), index]), time_cycle*60)]

            # Sensor signal calculation
            Sensor_signal[f'SS_{(index//2)+1}'] = [((Air_value/Gas_value) - 1) for Air_value, Gas_value in zip(first_3_min, second_3_min)]

        elif name == 'Transmittance':
            # Min values of air:
            first_3_min = [data.loc[(data.iloc[:, index] < (minutes_3_mark + search_delta)) & (data.iloc[:, index] > (minutes_3_mark - search_delta))].iloc[:, index+1].min() for minutes_3_mark in range(540, int(data.iloc[data.iloc[:, index].last_valid_index(), index]), time_cycle*60)]

            # Max values of gas:
            second_3_min = [data.loc[(data.iloc[:, index] < (minutes_3_mark + search_delta)) & (data.iloc[:, index] > (minutes_3_mark - search_delta))].iloc[:, index+1].max() for minutes_3_mark in range(720, int(data.iloc[data.iloc[:, index].last_valid_index(), index]), time_cycle*60)]

            # Sensor signal calculation
            Sensor_signal[f'SS_{(index//2)+1}'] = [((Gas_value/Air_value) - 1) for Air_value, Gas_value in zip(first_3_min, second_3_min)]
            
    return Sensor_signal


In [16]:
Optic_Sensor_signal = sensor_signal(optic_data, name='Transmittance')
Optic_Sensor_signal

SS_1      SS_2      SS_3
0  0.000015  0.000352  0.000437
1  0.000266  0.000308  0.000685
2  0.000385  0.000338  0.000744
3  0.000400  0.000441  0.000788
4  0.000444  0.000499  0.000862
5  0.000415  0.000529  0.000950
6  0.000415  0.000617  0.000731
7  0.000281  0.000470  0.001039
8  0.000385  0.000515  0.000644

In [17]:
# Calculating statistics of sensor signal
def ss_statistic(data: pd.DataFrame, humidity=[0, 30, 50]):
    SS_statistic = pd.DataFrame()
    SS_statistic['Humidity'] = humidity

    for index in range(0, len(data.columns)):
        SS_statistic.loc[index, 'mean'] = data.describe().iloc[1, index]
        SS_statistic.loc[index, 'std'] = data.describe().iloc[2, index]

    SS_statistic = SS_statistic.set_index('Humidity')    
    return SS_statistic

In [18]:
SS_optic_statistic = ss_statistic(Optic_Sensor_signal)
SS_optic_statistic

mean       std
Humidity                    
0         0.000334  0.000134
30        0.000452  0.000102
50        0.000764  0.000177

In [19]:
def statistics_plot(data):
    fig = px.scatter(data, y = 'mean', error_y = 'std', trendline = 'ols', color_discrete_sequence=['darkblue'])
    results = px.get_trendline_results(fig).iloc[0]["px_fit_results"]
    a = results.params[1]
    b = results.params[0]
    R2 = results.rsquared

    # Updating layout data
    fig.update_layout(font_size = 15,
                        title = f'Optical Sensor signal statistics <br>y = {a:.3f}x + {b:.3f}, R<sup>2</sup> = {R2:.2f}',
                        legend_title = "Measurement<br>parameters",
                        legend_font_size = 15,
                        xaxis_title = "Humidity, %",
                        yaxis_title = "Mean Sensor Signal \u0394T / T0",
                        #yaxis_type = 'log',
                        plot_bgcolor = 'rgba(250,250,250,1)',
                        width = 950,
                        height = 650,
                        )
    fig.add_shape(type="rect",
                    xref="paper",
                    yref="paper",
                    x0=0,
                    y0=0,
                    x1=1.0,
                    y1=1.0,
            line=dict(
                color="black",
                    width=1,))
    fig.show()

In [20]:
statistics_plot(SS_optic_statistic)

---

### Computing LOD (Limit of Detection)

In [21]:
# you can use any filter, starting from moving average and LOWESS. Here is an exemplar implementation of Savitzky-Golay filter
def smooth(raw_data: pd.Series, window_length: int = 100, polyorder: int = 3) -> (pd.Series, list):
  index = raw_data.index.values
  filtered = savgol_filter(raw_data, window_length = window_length, polyorder = polyorder, mode = 'mirror')
  noise = [x - y for x, y in zip(filtered, raw_data.values.tolist())]
  return pd.Series(data = filtered, index = index), noise

In [22]:
def LOD_calculation(data: pd.DataFrame, Sensor_signal: pd.DataFrame, name, Gas_ppm=50, search_delta=60, time_cycle=3, humidity=[0, 30, 50]):
    LOD_data = pd.DataFrame()
    # Extracting Noise data
    for index, humid in zip(range(0, len(data.columns), 2), humidity):
        smooth_data, Noise = smooth(data.iloc[:, index+1], 70)
        Noise = pd.DataFrame(Noise).dropna()
        RMSE_value = np.sqrt(sum([(x - Noise.mean()) ** 2 for x in Noise]) / len(Noise))

        
        if name == 'Resistance':
            # Computing mean Air_transmittance:
            Air_value = [data.loc[(data.iloc[:, index] < (minutes_3_mark + search_delta)) & (data.iloc[:, index] > (minutes_3_mark - search_delta))].iloc[:, index+1].max() for minutes_3_mark in range(180, int(data.iloc[data.iloc[:, index].last_valid_index(), index]), time_cycle*60)]
            
            # Computing SS_LOD:
            SS_LOD = (3*RMSE_value) / np.mean(Air_value)
            # Computing LOD:
            LOD_data[humid] = ((SS_LOD * Gas_ppm) / Sensor_signal.iloc[:, index//2].mean()) * 100

        elif name == 'Transmittance':
            # Computing mean Air_transmittance
            Air_value = [data.loc[(data.iloc[:, index] < (minutes_3_mark + search_delta)) & (data.iloc[:, index] > (minutes_3_mark - search_delta))].iloc[:, index+1].min() for minutes_3_mark in range(180, int(data.iloc[data.iloc[:, index].last_valid_index(), index]), time_cycle*60)]

            # Computing SS_LOD:
            SS_LOD = (3*RMSE_value) / np.mean(Air_value)
            # Computing LOD:
            LOD_data[humid] = ((SS_LOD * Gas_ppm) / Sensor_signal.iloc[:, index//2].mean()) * 100
     
    return LOD_data

In [23]:
LOD_data = LOD_calculation(optic_data, Optic_Sensor_signal, name='Transmittance')
LOD_data

0         30        50
0  0.170999  0.397378  0.398505

---

# DATA Processing

### Resistance Response

### Loading data

In [24]:
# Function for cleaning
def Resistance_data(file_names: list) -> pd.DataFrame:
    dt = pd.DataFrame()
    for name, index in zip(file_names, np.arange(1, len(file_names)+1)):
        data_resist_response = pd.read_excel(f'{name}', header = None)
        data_resist_response = data_resist_response.rename(columns={'Unnamed: 3': 'Resistance', 'Unnamed: 0': 'Time'})
        dt[f'resist_response_{index}_Time_s'] = data_resist_response.iloc[7:, 0].reset_index().drop(['index'], axis=1).astype(float)
        dt[f'resist_response_{index}_Resistance_Ohms'] = data_resist_response.iloc[7:, 3].reset_index().drop(['index'], axis=1).astype(float)
    return dt

In [25]:
# Input parameters for PM320_data:
file_names_resist = [r'resist_data_20_09_23_new_CNT_HumAir_RH10.xlsx',
                     r'resist_data_20_09_23_new_CNT_HumAir_RH30.xlsx',
                     r'resist_data_20_09_23_new_CNT_HumAir_RH50.xlsx',]

In [26]:
resist_data = Resistance_data(file_names_resist)
resist_data.head()

resist_response_1_Time_s  resist_response_1_Resistance_Ohms  \
0                     0.000                        3603.360783   
1                     1.269                        3608.831533   
2                     1.675                        3599.723685   
3                     2.089                        3605.182089   
4                     2.493                        3605.182089   

   resist_response_2_Time_s  resist_response_2_Resistance_Ohms  \
0                     0.000                        3148.366785   
1                     1.291                        3152.542384   
2                     1.702                        3144.202233   
3                     2.117                        3148.366785   
4                     2.521                        3149.758083   

   resist_response_3_Time_s  resist_response_3_Resistance_Ohms  
0                     0.000                        2923.760318  
1                     1.234                        2917.778462  
2                     1.641                        2922.562327  
3                     2.061                        2924.959292  
4                     2.474                        2922.562327

### Resistance Normalization

In [27]:
# Function for creating transmittance data PM100D
def Resistance_create_data(data: pd.DataFrame):
    Resistance_norm = pd.DataFrame()
    count = 1
    for n in np.arange(0, len(data.columns), 2):
        Resistance_0 = data.iloc[0, n+1]
        Resistance_norm[f'Resist_response_{count}_R_Norm'] = (data.iloc[:, n+1] - Resistance_0) / Resistance_0
        count += 1
    return Resistance_norm

# Function for creating time data
def Time_create_data(data):
    Time = pd.DataFrame()
    count = 1
    for n in np.arange(0, len(data.columns), 2):
        Time[f'{count}_Time'] = data.iloc[:, n]
        count += 1
    return Time

In [28]:
Resistance_norm_data = Resistance_create_data(resist_data)
Resistance_norm_data.head()

Resist_response_1_R_Norm  Resist_response_2_R_Norm  \
0                  0.000000                  0.000000   
1                  0.001518                  0.001326   
2                 -0.001009                 -0.001323   
3                  0.000505                  0.000000   
4                  0.000505                  0.000442   

   Resist_response_3_R_Norm  
0                  0.000000  
1                 -0.002046  
2                 -0.000410  
3                  0.000410  
4                 -0.000410

In [29]:
Time_data_R = Time_create_data(resist_data)
Time_data_R.head()

1_Time  2_Time  3_Time
0   0.000   0.000   0.000
1   1.269   1.291   1.234
2   1.675   1.702   1.641
3   2.089   2.117   2.061
4   2.493   2.521   2.474

In [30]:
# plotting raw data
def quick_plot_R(data: pd.DataFrame, Time_data, time_cycle) -> None:
    fig = go.Figure()
    
    # Making colour for each data
    humidity = [10, 30, 50]
    color_dict = dict(zip(humidity, sample_colorscale('Portland', minmax_scale(humidity))))

    # Creating line plots from data
    for column, humid, count in zip(data.columns.values, humidity, np.arange(0, len(data.columns.values), 1)):
        minutes = Time_data.iloc[:, count].values / 60
        fig.add_trace(go.Scattergl(x = minutes, 
                                   y = data.loc[:,column].values, 
                                   name = str(f'{humid}% humidity'),
                                   line_color = color_dict[humid]))

    # Creating vertical rectangles
    for i in np.arange(time_cycle/2 +0.15, max(Time_data.max())/60, time_cycle):
        fig.add_vrect(x0=i,
                      x1=i + 3,
                      line_width=0,
                      fillcolor='grey',
                      opacity=0.1,
                      annotation_text='<i>H<sub>2</sub></i>O',
                      annotation_font_size=20,
                      annotation_textangle=270,
                      annotation_position='top',)

    # Updating layout data
    fig.update_layout(font_size = 15,
                      title = f"CNT film T=80%, S11=1.5 \u03BCm.   date: 20.09.23 <br>Mixture: Air (100 sccm) <--> Dry Air + Humid Air",
                      legend_title = "Measurement<br>parameters",
                      legend_font_size = 15,
                      xaxis_title = "Time, min",
                      yaxis_title = "Resistance, \u0394R / R0",
                      #yaxis_type = 'log',
                      plot_bgcolor = 'rgba(250,250,250,1)',
                      width = 950,
                      height = 650,
                      )
    fig.add_shape(type="rect",
                  xref="paper",
                  yref="paper",
                  x0=0,
                  y0=0,
                  x1=1.0,
                  y1=1.0,
            line=dict(
                color="black",
                 width=1,))
    fig.show()

In [31]:
quick_plot_R(Resistance_norm_data, Time_data_R, time_cycle)

---

### Violin Plots

In [32]:
def print_dt_metrics(Time_data: pd.DataFrame, humidity=[0, 30, 50]):
    try:
        dt = Time_data.diff().dropna()
        time_dt = pd.DataFrame()
        for index, humid in zip(range(0, len(Time_data.columns)), humidity):
            # dt - time between two neighboring datapoints [in seconds]
            time_dt.loc[f'{humid}', 'mean'] = dt.describe().iloc[1, index]
            time_dt.loc[f'{humid}', 'std'] = dt.describe().iloc[2, index]
            
            MAPE = mean_absolute_percentage_error(dt.iloc[:, index], np.array([dt.describe().iloc[1, index]] * len(dt)))
            time_dt.loc[f'{humid}', 'MAPE'] = MAPE * 100 # in percentages %
        
        return time_dt
    except AttributeError:
        print("Cannot calculate metrics: no Time_sec column. Wrong dataframe? Need raw dataframe from load_data")

In [33]:
print_dt_metrics(Time_data_R)

mean       std      MAPE
0   0.401599  0.013133  1.905017
30  0.406667  0.011720  1.325267
50  0.407146  0.011293  1.338222

In [34]:
def violin_plot(Time_data: pd.DataFrame):
  data_metrics = print_dt_metrics(Time_data)
  for index in range(0, len(Time_data.columns)):

    fig = px.scatter(x = Time_data.iloc[1:, index].dropna(), y = Time_data.diff().iloc[:, index].dropna(), marginal_y = "violin")
    # Updating layout data
    fig.update_layout(font_size = 15,
                      title = f"dt = {data_metrics.iloc[index, 0]:.2f} \u00b1 {data_metrics.iloc[index, 1]:.3f} seconds <br> MAPE = {data_metrics.iloc[index, 2]:.2f} %",
                      title_x=0.5,
                      legend_title = "Measurement<br>parameters",
                      legend_font_size = 15,
                      xaxis_title = "Time, s",
                      yaxis_title = "Time difference between datapoints, s",
                      hovermode = False,
                      plot_bgcolor = 'rgba(250,250,250,1)',
                      width = 1200,
                      height = 650,
                      )
    fig.add_shape(type="rect",
                  xref="paper",
                  yref="paper",
                  x0=0,
                  y0=0,
                  x1=1.0,
                  y1=1.0,
            line=dict(
                color="black",
                 width=1,))

    fig.show()

In [35]:
violin_plot(Time_data_R.iloc[1:, :])

---

### Computing Sensor Signal

In [36]:
def sensor_signal(data: pd.DataFrame, name, search_delta=60):
        
    Sensor_signal = pd.DataFrame()
    for index in range(0, len(data.columns), 2):

        #Calculating Sensor signal
        if name == 'Resistance':
            # Min values of air:
            first_3_min = [data.loc[(data.iloc[:, index] < (minutes_3_mark + search_delta)) & (data.iloc[:, index] > (minutes_3_mark - search_delta))].iloc[:, index+1].max() for minutes_3_mark in range(540, int(data.iloc[data.iloc[:, index].last_valid_index(), index]), time_cycle*60)]

            # Max values of gas:
            second_3_min = [data.loc[(data.iloc[:, index] < (minutes_3_mark + search_delta)) & (data.iloc[:, index] > (minutes_3_mark - search_delta))].iloc[:, index+1].min() for minutes_3_mark in range(720, int(data.iloc[data.iloc[:, index].last_valid_index(), index]), time_cycle*60)]

            # Sensor signal calculation
            Sensor_signal[f'SS_{(index//2)+1}'] = [((Air_value/Gas_value) - 1) for Air_value, Gas_value in zip(first_3_min, second_3_min)]

        elif name == 'Transmittance':
            # Min values of air:
            first_3_min = [data.loc[(data.iloc[:, index] < (minutes_3_mark + search_delta)) & (data.iloc[:, index] > (minutes_3_mark - search_delta))].iloc[:, index+1].min() for minutes_3_mark in range(540, int(data.iloc[data.iloc[:, index].last_valid_index(), index]), time_cycle*60)]

            # Max values of gas:
            second_3_min = [data.loc[(data.iloc[:, index] < (minutes_3_mark + search_delta)) & (data.iloc[:, index] > (minutes_3_mark - search_delta))].iloc[:, index+1].max() for minutes_3_mark in range(720, int(data.iloc[data.iloc[:, index].last_valid_index(), index]), time_cycle*60)]

            # Sensor signal calculation
            Sensor_signal[f'SS_{(index//2)+1}'] = [((Gas_value/Air_value) - 1) for Air_value, Gas_value in zip(first_3_min, second_3_min)]
            
    return Sensor_signal


In [37]:
Resist_Sensor_signal = sensor_signal(resist_data, name='Resistance')
Resist_Sensor_signal

SS_1      SS_2      SS_3
0  0.002549  0.004984  0.012669
1  0.005120  0.006871  0.014085
2  0.006151  0.007838  0.016832
3  0.006148  0.007874  0.016486
4  0.005629  0.008837  0.016572
5  0.007161  0.010280  0.017090
6  0.006129  0.009359  0.017613
7  0.007150  0.009372  0.018118
8  0.006116  0.009394  0.019069

In [38]:
# Calculating statistics of sensor signal
def ss_statistic(data: pd.DataFrame, humidity=[0, 30, 50]):
    SS_statistic = pd.DataFrame()
    SS_statistic['Humidity'] = humidity

    for index in range(0, len(data.columns)):
        SS_statistic.loc[index, 'mean'] = data.describe().iloc[1, index]
        SS_statistic.loc[index, 'std'] = data.describe().iloc[2, index]

    SS_statistic = SS_statistic.set_index('Humidity')    
    return SS_statistic

In [39]:
SS_resist_statistic = ss_statistic(Resist_Sensor_signal, [10, 30, 50])
SS_resist_statistic

mean       std
Humidity                    
10        0.005795  0.001378
30        0.008312  0.001624
50        0.016504  0.001982

### Sensor Signal Visualization

In [40]:
def statistics_plot(data):
    fig = px.scatter(data, y = 'mean', error_y = 'std', trendline = 'ols', color_discrete_sequence=['darkblue'])
    results = px.get_trendline_results(fig).iloc[0]["px_fit_results"]
    a = results.params[1]
    b = results.params[0]
    R2 = results.rsquared

    # Updating layout data
    fig.update_layout(font_size = 15,
                        #title = f'Resistive Sensor signal statistics <br>y = {a:.3f}x + {b:.3f}, R<sup>2</sup> = {R2:.2f}',
                        legend_title = "Measurement<br>parameters",
                        legend_font_size = 15,
                        xaxis_title = "Humidity, %",
                        yaxis_title = "Mean Sensor Signal \u0394R / R0",
                        #yaxis_type = 'log',
                        plot_bgcolor = 'rgba(250,250,250,1)',
                        width = 950,
                        height = 650,
                        )
    fig.add_shape(type="rect",
                    xref="paper",
                    yref="paper",
                    x0=0,
                    y0=0,
                    x1=1.0,
                    y1=1.0,
            line=dict(
                color="black",
                    width=1,))
    fig.show()

In [41]:
statistics_plot(SS_resist_statistic)

---

### Computing LOD

In [42]:
# you can use any filter, starting from moving average and LOWESS. Here is an exemplar implementation of Savitzky-Golay filter
def smooth(raw_data: pd.Series, window_length: int = 100, polyorder: int = 3) -> (pd.Series, list):
  index = raw_data.index.values
  filtered = savgol_filter(raw_data, window_length = window_length, polyorder = polyorder, mode = 'mirror')
  noise = [x - y for x, y in zip(filtered, raw_data.values.tolist())]
  return pd.Series(data = filtered, index = index), noise

In [43]:
def LOD_calculation(data: pd.DataFrame, Sensor_signal: pd.DataFrame, name, Gas_ppm=50, search_delta=60, time_cycle=3, humidity=[0, 30, 50]):
    LOD_data = pd.DataFrame()
    # Extracting Noise data
    for index, humid in zip(range(0, len(data.columns), 2), humidity):
        smooth_data, Noise = smooth(data.iloc[:, index+1], 70)
        Noise = pd.DataFrame(Noise).dropna()
        RMSE_value = np.sqrt(sum([(x - Noise.mean()) ** 2 for x in Noise]) / len(Noise))

        
        if name == 'Resistance':
            # Computing mean Air_transmittance:
            Air_value = [data.loc[(data.iloc[:, index] < (minutes_3_mark + search_delta)) & (data.iloc[:, index] > (minutes_3_mark - search_delta))].iloc[:, index+1].max() for minutes_3_mark in range(180, int(data.iloc[data.iloc[:, index].last_valid_index(), index]), time_cycle*60)]
            
            # Computing SS_LOD:
            SS_LOD = (3*RMSE_value) / np.mean(Air_value)
            # Computing LOD:
            LOD_data[humid] = ((SS_LOD * Gas_ppm) / Sensor_signal.iloc[:, index//2].mean()) * 100

        elif name == 'Transmittance':
            # Computing mean Air_transmittance
            Air_value = [data.loc[(data.iloc[:, index] < (minutes_3_mark + search_delta)) & (data.iloc[:, index] > (minutes_3_mark - search_delta))].iloc[:, index+1].min() for minutes_3_mark in range(180, int(data.iloc[data.iloc[:, index].last_valid_index(), index]), time_cycle*60)]

            # Computing SS_LOD:
            SS_LOD = (3*RMSE_value) / np.mean(Air_value)
            # Computing LOD:
            LOD_data[humid] = ((SS_LOD * Gas_ppm) / Sensor_signal.iloc[:, index//2].mean()) * 100
     
    return LOD_data

In [44]:
LOD_data = LOD_calculation(resist_data, Resist_Sensor_signal, name='Resistance')
LOD_data

0         30        50
0  0.00864  0.063829  0.039378

---